In [3]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import dgl
from dgl.nn import ChebConv
import networkx as nx
import networkx.algorithms.community as nx_comm
import numpy as np
import pandas as pd
import numpy.linalg as alg
import os
from tqdm import tqdm
from functools import reduce
import argparse




In [4]:

path = 'Dataset/socfb-Stanford3.mtx'

df = pd.read_table(path, skiprows=1, names = ["source", "target"], sep=" ")
g = nx.from_pandas_edgelist(df)

# calculate basic elements
num_nodes = g.number_of_nodes()
num_edges = g.number_of_edges()
degs = [g.degree[i] for i in g.nodes]
avg_deg = sum(degs)/len(degs)

res = 10


# clustering
# generally, we fix the outcome of clustering
clusters = nx_comm.louvain_communities(g, seed = 10, resolution=res)
clusters = sorted(clusters, key = len, reverse=True)
cluster_sizes = list(map(len, clusters))
num_cluster = len(clusters)

# dict: from node to its cluster
inverse_cluster_dict = {
    node: cl for cl in range(num_cluster) for node in clusters[cl]
}

# dict: from node to its connected cluster
node_to_connected_clusters = {
    node: node_connects_cluster(node) for node in range(1, num_nodes + 1)
}


for i in g.nodes:
    g.nodes[i]["deg"] = g.degree[i]

rev_cluster_sizes = cluster_sizes[::-1]
rev_clusters = clusters[::-1]
rev_cluster_sizes = np.array(rev_cluster_sizes)

def node_connects_cluster(node):
    return set(map(lambda x: inverse_cluster_dict[x], list(g[node]))).union(set([inverse_cluster_dict[node]]))


In [5]:
dgl_G = dgl.from_networkx(g)

In [6]:
ramps = [0.02, 0.05, 0.1, 0.25, 0.5]
repeat_num = 1000

In [7]:

class GCN(nn.Module):
    def __init__(self):
        super().__init__()
        self.conv1 = dgl.nn.ChebConv(2, 16, 2)
        self.conv2 = dgl.nn.ChebConv(16, 16, 1)
        self.conv3 = dgl.nn.ChebConv(16, 1, 1)
        
    def forward(self, g, features):
        x = self.conv1(g, features)
        x = self.conv2(g, x)
        x = self.conv3(g, x)
        return x
        

In [8]:
A = np.array(nx.adjacency_matrix(g).todense(), dtype = np.float64)
deg_array = np.array(list(dict(g.degree).values()))

D_inv_A = np.zeros_like(A)

for i in range(num_nodes):
    D_inv_A[i] = A[i] / deg_array[i]


In [9]:
multi_hop_A = np.linalg.matrix_power(D_inv_A, 2)
# torch.save(multi_hop_A, "A_2hop.pkl")
# multi_hop_A = torch.load("A_2hop.pkl")

In [74]:
# set diagonal of 2-hop adjacency to 0
for i in range(num_nodes):
    multi_hop_A[i, i] = 0

In [27]:
node_list = list(g.nodes.keys())

In [76]:
def po_2hop_linear_model(graph, z_vec, alpha=1, beta=1, sigma=0.1, gamma=1, r1=1, r2=0.5):        
    y_vec = alpha + beta * z_vec + sigma * np.random.normal(size=(num_nodes, 1)) + gamma * (
    r1 * np.matmul(D_inv_A, z_vec) + r2 * np.matmul(multi_hop_A, z_vec)
)
    
    for i in range(num_nodes):
        graph.nodes[node_list[i]]["y"] = y_vec[i][0]
        graph.nodes[node_list[i]]["z"] = z_vec[i][0]

In [ ]:
# cluster-level cr

repeat_num = 1000

GATE_hat_list = np.zeros((repeat_num, len(ramps)))

     
for seed in tqdm(range(repeat_num)):
# for seed in tqdm(range(151, repeat_num)): # interupted at 151
    
    np.random.seed(seed)      
    rollout_index = np.random.uniform(0, 1, size=(num_nodes))   
    
    for num_step in range(len(ramps)): 
        print(f"Seed: {seed}")           
        torch.manual_seed(2)
        p_list = ramps[num_step:]                 
        g_feat_list = []
        y_list = []
                
        for p in p_list:        
            z_vector = (rollout_index <= np.quantile(rollout_index, p)).astype(int) # unit-level
            po_2hop_linear_model(g, z_vector.reshape(-1,1)) # add dimension            
            g_feat_list.append(torch.tensor([[g.nodes[n]['z'], g.nodes[n]['deg']] for n in g.nodes], dtype=torch.float))
            y_list.append(torch.tensor([[g.nodes[n]['y']] for n in g.nodes], dtype=torch.float).reshape(-1))
    
        # Instantiate the model and optimizer
        model = GCN()    
        optimizer = torch.optim.Adam(model.parameters(), lr=0.004)
        
        # Train the model
        for epoch in range(400):
            for i in range(len(p_list)):
                model.train()
                optimizer.zero_grad()
                out = model(dgl_G, g_feat_list[i])
                loss = F.mse_loss(out.squeeze(), y_list[i])  
                loss.backward()
                optimizer.step()
            
                if epoch % 50 == 0:
                    print(f'Epoch {epoch}, Treat Prop: {p_list[i]:.2f}, Loss: {loss:.4f}')
    
        print(loss.item())
        g_feat = g_feat_list[0]
    
        g_feat[:,0] = 0
        global_control_pred = model(dgl_G, g_feat).detach().numpy()
    
        g_feat[:,0] = 1
        global_treat_pred = model(dgl_G, g_feat).detach().numpy()
    
        GATE_hat = global_treat_pred.mean() - global_control_pred.mean()
    
        GATE_hat_list[seed, num_step] = GATE_hat
        
    torch.save(GATE_hat_list, "Result/2hop_CR_unit.pkl")


  0%|          | 0/1000 [00:00<?, ?it/s]

Seed: 0


/root/miniconda3/envs/myconda/lib/python3.10/site-packages/dgl/nn/pytorch/conv/chebconv.py:108: DGLWarning: lambda_max is not provided, using default value of 2.  Please use dgl.laplacian_lambda_max to compute the eigenvalues.
  dgl_warning(


Epoch 0, Treat Prop: 0.02, Loss: 7.9782
Epoch 0, Treat Prop: 0.05, Loss: 2.3736
Epoch 0, Treat Prop: 0.10, Loss: 1.3305
Epoch 0, Treat Prop: 0.25, Loss: 2.2232
Epoch 0, Treat Prop: 0.50, Loss: 4.2137
Epoch 50, Treat Prop: 0.02, Loss: 0.1425
Epoch 50, Treat Prop: 0.05, Loss: 0.1708
Epoch 50, Treat Prop: 0.10, Loss: 0.0928
Epoch 50, Treat Prop: 0.25, Loss: 0.1969
Epoch 50, Treat Prop: 0.50, Loss: 0.6540
Epoch 100, Treat Prop: 0.02, Loss: 0.0351
Epoch 100, Treat Prop: 0.05, Loss: 0.0507
Epoch 100, Treat Prop: 0.10, Loss: 0.0309
Epoch 100, Treat Prop: 0.25, Loss: 0.0577
Epoch 100, Treat Prop: 0.50, Loss: 0.1084
Epoch 150, Treat Prop: 0.02, Loss: 0.0298
Epoch 150, Treat Prop: 0.05, Loss: 0.0386
Epoch 150, Treat Prop: 0.10, Loss: 0.0276
Epoch 150, Treat Prop: 0.25, Loss: 0.0593
Epoch 150, Treat Prop: 0.50, Loss: 0.0965
Epoch 200, Treat Prop: 0.02, Loss: 0.0339
Epoch 200, Treat Prop: 0.05, Loss: 0.0364
Epoch 200, Treat Prop: 0.10, Loss: 0.0282
Epoch 200, Treat Prop: 0.25, Loss: 0.0634
Epoch 2

  0%|          | 1/1000 [00:25<6:57:10, 25.06s/it]

...

Seed: 708
Epoch 0, Treat Prop: 0.02, Loss: 7.9779
Epoch 0, Treat Prop: 0.05, Loss: 2.3591
Epoch 0, Treat Prop: 0.10, Loss: 1.3248
Epoch 0, Treat Prop: 0.25, Loss: 2.2520
Epoch 0, Treat Prop: 0.50, Loss: 4.2482
Epoch 50, Treat Prop: 0.02, Loss: 0.1503
Epoch 50, Treat Prop: 0.05, Loss: 0.1783
Epoch 50, Treat Prop: 0.10, Loss: 0.1137
Epoch 50, Treat Prop: 0.25, Loss: 0.2021
Epoch 50, Treat Prop: 0.50, Loss: 0.6873
Epoch 100, Treat Prop: 0.02, Loss: 0.0395
Epoch 100, Treat Prop: 0.05, Loss: 0.0547
Epoch 100, Treat Prop: 0.10, Loss: 0.0329
Epoch 100, Treat Prop: 0.25, Loss: 0.0623
Epoch 100, Treat Prop: 0.50, Loss: 0.1188
Epoch 150, Treat Prop: 0.02, Loss: 0.0361
Epoch 150, Treat Prop: 0.05, Loss: 0.0380
Epoch 150, Treat Prop: 0.10, Loss: 0.0283
Epoch 150, Treat Prop: 0.25, Loss: 0.0610
Epoch 150, Treat Prop: 0.50, Loss: 0.0955
Epoch 200, Treat Prop: 0.02, Loss: 0.0355
Epoch 200, Treat Prop: 0.05, Loss: 0.0346
Epoch 200, Treat Prop: 0.10, Loss: 0.0286
Epoch 200, Treat Prop: 0.25, Loss: 0.06

 71%|███████   | 709/1000 [4:59:16<2:00:49, 24.91s/it]

Seed: 709
Epoch 0, Treat Prop: 0.02, Loss: 8.0144
Epoch 0, Treat Prop: 0.05, Loss: 2.3831
Epoch 0, Treat Prop: 0.10, Loss: 1.3222
Epoch 0, Treat Prop: 0.25, Loss: 2.2526
Epoch 0, Treat Prop: 0.50, Loss: 4.2555
Epoch 50, Treat Prop: 0.02, Loss: 0.1697
Epoch 50, Treat Prop: 0.05, Loss: 0.2159
Epoch 50, Treat Prop: 0.10, Loss: 0.1198
Epoch 50, Treat Prop: 0.25, Loss: 0.2033
Epoch 50, Treat Prop: 0.50, Loss: 0.7346
Epoch 100, Treat Prop: 0.02, Loss: 0.0354
Epoch 100, Treat Prop: 0.05, Loss: 0.0502
Epoch 100, Treat Prop: 0.10, Loss: 0.0297
Epoch 100, Treat Prop: 0.25, Loss: 0.0577
Epoch 100, Treat Prop: 0.50, Loss: 0.1096
Epoch 150, Treat Prop: 0.02, Loss: 0.0288
Epoch 150, Treat Prop: 0.05, Loss: 0.0354
Epoch 150, Treat Prop: 0.10, Loss: 0.0266
Epoch 150, Treat Prop: 0.25, Loss: 0.0576
Epoch 150, Treat Prop: 0.50, Loss: 0.0970
Epoch 200, Treat Prop: 0.02, Loss: 0.0328
Epoch 200, Treat Prop: 0.05, Loss: 0.0336
Epoch 200, Treat Prop: 0.10, Loss: 0.0271
Epoch 200, Treat Prop: 0.25, Loss: 0.06

 71%|███████   | 710/1000 [4:59:41<1:59:54, 24.81s/it]

Seed: 710
Epoch 0, Treat Prop: 0.02, Loss: 7.9783
Epoch 0, Treat Prop: 0.05, Loss: 2.3720
Epoch 0, Treat Prop: 0.10, Loss: 1.3265
Epoch 0, Treat Prop: 0.25, Loss: 2.2385
Epoch 0, Treat Prop: 0.50, Loss: 4.2338
Epoch 50, Treat Prop: 0.02, Loss: 0.1491
Epoch 50, Treat Prop: 0.05, Loss: 0.1781
Epoch 50, Treat Prop: 0.10, Loss: 0.1227
Epoch 50, Treat Prop: 0.25, Loss: 0.2139
Epoch 50, Treat Prop: 0.50, Loss: 0.7093
Epoch 100, Treat Prop: 0.02, Loss: 0.0408
Epoch 100, Treat Prop: 0.05, Loss: 0.0590
Epoch 100, Treat Prop: 0.10, Loss: 0.0319
Epoch 100, Treat Prop: 0.25, Loss: 0.0654
Epoch 100, Treat Prop: 0.50, Loss: 0.1178
Epoch 150, Treat Prop: 0.02, Loss: 0.0305
Epoch 150, Treat Prop: 0.05, Loss: 0.0386
Epoch 150, Treat Prop: 0.10, Loss: 0.0269
Epoch 150, Treat Prop: 0.25, Loss: 0.0585
Epoch 150, Treat Prop: 0.50, Loss: 0.0957
Epoch 200, Treat Prop: 0.02, Loss: 0.0299
Epoch 200, Treat Prop: 0.05, Loss: 0.0356
Epoch 200, Treat Prop: 0.10, Loss: 0.0269
Epoch 200, Treat Prop: 0.25, Loss: 0.05